In [7]:
from pygcj.pygcj import GCJProj
import pandas as pd
import folium

## read data as pandas dataframe

In [3]:
input_df = pd.read_csv(r"/data-sat-img/postprocessed/mujiang/stations_with_geo_gaode_20240207.csv")
input_df.head()

section_id station_zh   line_zh                 line_en construction_start  \
0           1       罗山路站  上海地铁16号线  Shanghai Metro Line 16            2010.03   
1           1       周浦东站  上海地铁16号线  Shanghai Metro Line 16            2010.03   
2           1      鹤沙航城站  上海地铁16号线  Shanghai Metro Line 16            2010.03   
3           1       航头东站  上海地铁16号线  Shanghai Metro Line 16            2010.03   
4           1        新场站  上海地铁16号线  Shanghai Metro Line 16            2010.03   

   construction_end opening_date  close_date  \
0           2013.04      2013.12         NaN   
1           2013.04      2013.12         NaN   
2           2013.04      2013.12         NaN   
3           2013.04      2013.12         NaN   
4           2013.04      2013.12         NaN   

   first_planning_or_public_announcement  approval_by_national_government  \
0                                2005.11                          2009.04   
1                                2005.11                          2009.04   
2                                2005.11                          2009.04   
3                                2005.11                          2009.04   
4                                2005.11                          2009.04   

   approval_by_local_or_provincial_goverment                      geo  
0                                        NaN  c(121.589223,31.162995)  
1                                        NaN  c(121.605689,31.111423)  
2                                        NaN  c(121.608918,31.077281)  
3                                        NaN  c(121.593057,31.033702)  
4                                        NaN  c(121.653461,31.026120)

## reading coordinates and transform to wgs1984

In [5]:
input_df['geo'] = input_df['geo'].str.split('\(|\)', expand=True)[1]
input_df['geo_x'] = input_df['geo'].str.split(',', expand=True)[0].astype(float)
input_df['geo_y'] = input_df['geo'].str.split(',', expand=True)[1].astype(float)

In [6]:
wgs_lat_list = []
wgs_lon_list = []

trans = GCJProj()
for index, row in input_df.iterrows():
    if (row["geo_y"]<150):
        wgs_lat, wgs_lon = trans.gcj_to_wgs(row["geo_y"],row["geo_x"])
        
    else:
        wgs_lat = 0
        wgs_lon = 0
        
    wgs_lat_list.append(wgs_lat)
    wgs_lon_list.append(wgs_lon)
    
input_df["wgs_lon"] = wgs_lon_list
input_df["wgs_lat"] = wgs_lat_list

### save result

In [30]:
input_df.to_csv(r"/data-sat-img/postprocessed/mujiang/" + "station_transformed.csv",encoding = "utf-8-sig",index = False)

## create interactive map using folium

In [21]:
map = folium.Map(location=[35.86166, 104.195397], zoom_start=4)

# Add circle markers to the map for each row in the DataFrame
for index, row in input_df.iterrows():
    folium.CircleMarker(
        [row['wgs_lat'], row['wgs_lon']],
        radius=5,  # Size of the circle marker
        weight=2, #the width of the stroke in pixels
        color='black',  # Border color of the circle marker
        fill=True,
        fill_color='red',  # Fill color of the circle marker
        fill_opacity=0.7,  # Fill opacity of the circle marker
        popup=row["line_en"] # Popup text for the marker
    ).add_to(map)

    
map